In [1]:
from sklearn import svm
from sklearn.naive_bayes import BernoulliNB
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix, classification_report,classification
from sklearn.ensemble import BaggingClassifier,RandomForestClassifier,ExtraTreesClassifier,AdaBoostClassifier,GradientBoostingClassifier
from sklearn.tree import DecisionTreeClassifier
from nltk.corpus import stopwords
import pandas as pd

In [2]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Paul\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [3]:
from nltk import TweetTokenizer

In [4]:
#read pickled data
tweets = pd.read_pickle("../data/tweets_cleaned.pkl")

In [5]:
#baseline accuracy
tweets.informative.value_counts(1)

1    0.698523
0    0.301477
Name: informative, dtype: float64

In [6]:
#Name variables 

X = tweets[["tweet_text"]]
y = tweets["informative"]

#train test split
X_train, X_test, y_train, y_test = train_test_split(X,
                                                    y,
                                                    test_size=0.25,
                                                    random_state=42,
                                                    stratify=y)

In [7]:
# Load stopwords from NLTK and add custom words
mystopwords = stopwords.words('english')
mystopwords.extend(['hurricane','tornado','harvey','irma','joplin','sandy','maria',
                    'like','would','get','x200b','https','one','www','com','org','etc','could'])

In [8]:
# Naive Bayes Bernouilli with CVEC
tknzr = TweetTokenizer()
cvec = CountVectorizer(tokenizer=tknzr.tokenize,stop_words=mystopwords,
                       max_features=3000,max_df=1.0,min_df=2, 
                       ngram_range=(1,1))

# Fit  CountVectorizer on the training data and transform training data.
X_train_cvec = pd.DataFrame(cvec.fit_transform(X_train['tweet_text']).todense(),
                            columns = cvec.get_feature_names())
# Transform our testing data with the already-fit CountVectorizer.
X_test_cvec = pd.DataFrame(cvec.transform(X_test['tweet_text']).todense(),
                           columns = cvec.get_feature_names())

# instantiate and fit model 
nb = BernoulliNB(alpha=1)
nb.fit(X_train_cvec, y_train)

# Score model on the training set.
print('Naive Bayes model with Count Vectorizer')
print(f'Train data accuracy: {nb.score(X_train_cvec,y_train):.3f}')

# Score our model on the testing set.
print(f'Test data accuracy: {nb.score(X_test_cvec,y_test):.3f}')

Naive Bayes model with Count Vectorizer
Train data accuracy: 0.821
Test data accuracy: 0.764


In [9]:
# Naive Bayes Bernouilli with Tfidf
tvec = TfidfVectorizer(tokenizer=tknzr.tokenize,stop_words=None,max_features=3000,max_df=1.0,min_df=2, ngram_range=(1,1))

# Fit our CountVectorizer on the training data and transform training data.
X_train_tvec = pd.DataFrame(tvec.fit_transform(X_train['tweet_text']).todense(),
                            columns = tvec.get_feature_names())
# Transform our testing data with the already-fit CountVectorizer.
X_test_tvec = pd.DataFrame(tvec.transform(X_test['tweet_text']).todense(),
                           columns = tvec.get_feature_names())

# instantiate and fit model 
nb = BernoulliNB(alpha=1)
nb.fit(X_train_tvec, y_train)

# Score model on the training set.
print('Naive Bayes model with TF-IDF Vectorizer')
print(f'Train data accuracy: {nb.score(X_train_tvec,y_train):.3f}')

# Score our model on the testing set.
print(f'Test data accuracy: {nb.score(X_test_tvec,y_test):.3f}')

Naive Bayes model with TF-IDF Vectorizer
Train data accuracy: 0.823
Test data accuracy: 0.784


In [37]:
# SVM model with CVEC
cvec = CountVectorizer(stop_words=mystopwords,max_features=300, ngram_range=(1,1))

# Fit  CountVectorizer on the training data and transform training data.
X_train_cvec = pd.DataFrame(cvec.fit_transform(X_train['tweet_text']).todense(),
                            columns = cvec.get_feature_names())
# Transform our testing data with the already-fit CountVectorizer.
X_test_cvec = pd.DataFrame(cvec.transform(X_test['tweet_text']).todense(),
                           columns = cvec.get_feature_names())
# Instantiate SVM.
# svc = svm.SVC(kernel='poly', C = 1.8, gamma = .05) 
svc = svm.SVC(kernel='rbf', C = 2, gamma = .2)  

# Fit on training data.
svc.fit(X_train_cvec,y_train)

# Score model on the training set.
print('Support Vector Machine model with Count Vectorizer')
print(f'Train data accuracy: {svc.score(X_train_cvec,y_train):.3f}')

# Score our model on the testing set.
print(f'Test data accuracy: {svc.score(X_test_cvec,y_test):.3f}')

Support Vector Machine model with Count Vectorizer
Train data accuracy: 0.809
Test data accuracy: 0.746


In [10]:
#CountVectorizer 
tknzr = TweetTokenizer()
cvec = CountVectorizer(stop_words="english", tokenizer=tknzr.tokenize)
X_train_cvec = pd.DataFrame(cvec.fit_transform(X_train['tweet_text']).todense(), columns = cvec.get_feature_names())
X_test_cvec = pd.DataFrame(cvec.transform(X_test['tweet_text']).todense(), columns = cvec.get_feature_names())
lr = LogisticRegression()
lr_model = lr.fit(X_train_cvec, y_train)
# Score model on the training set.
print('Logistic Regression model with Count Vectorizer and TweetTokenzer')
print(f'Train data accuracy: {lr.score(X_train_cvec,y_train):.3f}')

# Score our model on the testing set.
print(f'Test data accuracy: {lr.score(X_test_cvec,y_test):.3f}')

C:\Users\Paul\Anaconda3\envs\dsi\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


Logistic Regression model with Count Vectorizer and TweetTokenzer
Train data accuracy: 0.937
Test data accuracy: 0.807


In [ ]:
# KNN
model = KNeighborsClassifier(n_neighbors=5)
model.fit(X_train_cvec,y_train)
y_pred_train = model.predict(X_train_cvec)

print(f'Training R-sq is: {model.score(X_train,y_train):.3f}')
print(f'Testing R-sq is: {model.score(X_test,y_test):.3f}')

In [12]:
# random forest
model = RandomForestClassifier(max_depth=20,random_state=42,min_samples_leaf=5,n_estimators=10)
model.fit(X_train_cvec,y_train)
y_pred = model.predict(X_test_cvec)
y_pred_train = model.predict(X_train_cvec)

print(f'Training R-sq is: {model.score(X_train_cvec,y_train):.3f}')
print(f'Testing R-sq is: {model.score(X_test_cvec,y_test):.3f}')

Training R-sq is: 0.700
Testing R-sq is: 0.699


### Analyze Results of Best Model

In [41]:
# print confusion matrix
y_pred = lr.predict(X_test_cvec)
cm = confusion_matrix(y_test, y_pred)
cm_df = pd.DataFrame(cm, columns=['predict neg', 'predict pos'], index=['actual neg', 'actual pos'])
cm_df

predict neg  predict pos
actual neg          638          495
actual pos          231         2393

In [15]:
michael = pd.read_pickle('../data/hurricane_michael.pkl')

In [35]:
michael.shape

(50043, 13)

In [17]:
michael.head()

date  favorites geo  \
0 2018-10-12 23:59:57+00:00          4       
1 2018-10-12 23:59:53+00:00          1       
2 2018-10-12 23:59:52+00:00          0       
3 2018-10-12 23:59:49+00:00          0       
4 2018-10-12 23:59:43+00:00          0       

                                            hashtags                   id  \
0  #HurricaneMichael #blessed #UnitedWeStand #tal...  1050898900582838272   
1                                                     1050898882526371842   
2                         #HurricaneMichael #Florida  1050898882077442048   
3                                                     1050898865988222976   
4                  #HurricaneMichael #ExcessiveForce  1050898841879236608   

   mentions                                          permalink  retweets  \
0  @COTNews  https://twitter.com/joeearenas/status/10508989...         0   
1            https://twitter.com/LakesideBexley/status/1050...         0   
2            https://twitter.com/PRAISETRIUNEGOD/status/105...         0   
3            https://twitter.com/aShartee/status/1050898865...         0   
4            https://twitter.com/MindOfMo/status/1050898841...         0   

                                                text       to         username  
0  @COTNews has been working 24/7 to restore serv...     None       joeearenas  
1  In the wake of Hurricane Michael, we understan...     None   LakesideBexley  
2  Maybe 17 " #HurricaneMichael Updates: Body Fou...     None  PRAISETRIUNEGOD  
3  In other news praying for those affected by hu...     None         aShartee  
4  iSpy 2 or 3 who'd be hard-pressed to RUN in an...  CBSNews         MindOfMo

In [27]:
# convert text to lower case
michael['clean_text'] = michael['text'].str.lower()

In [28]:
# remove URLs
import re
michael['clean_text'] = michael['clean_text'].apply(lambda x: re.split('https:\/\/.*', str(x))[0])

In [29]:
#remove "RT" string
michael['clean_text'] = michael['clean_text'].map(lambda x: x.lstrip('rt'))

#remove remaining punctuation except for "#"
michael['clean_text'] = michael['clean_text'].str.replace("[^a-zA-Z]", " ")

In [30]:
# Transform out-of-event testing data with the already-fit CountVectorizer.
michael_cvec = pd.DataFrame(cvec.transform(michael['clean_text']).todense(),
                           columns = cvec.get_feature_names())


In [31]:
michael['inform_pred'] = lr_model.predict(michael_cvec)

In [32]:
michael.inform_pred.value_counts()

1    39943
0    10100
Name: inform_pred, dtype: int64

In [26]:
# michael.inform_pred.value_counts()  - before cleaning 200 more tweets were considered informative by model

1    40151
0     9892
Name: inform_pred, dtype: int64

In [37]:
# print uninformative tweets
mask = michael.inform_pred == 0
for tweet in michael[mask].clean_text:
    print(tweet)
    print('-----------------------------------')

maybe       hurricanemichael updates  body found on  florida beach with death toll already at     
-----------------------------------
ispy   or   who d be hard pressed to run in an emergency  i mention it cuz     potus is not honoring  hurricanemichael  wtf     suspect overweight unfit contributes to  excessiveforce  including especially fatally shooting fast     leo mostly giving heir carte blanche  like mbs  
-----------------------------------
ispy   or   who d be hard pressed to run in an emergency  i mention it cuz     potus is not honoring  hurricanemichael  wtf     suspect overweight unfit contributes to  excessiveforce  including especially fatally shooting fast     leo mostly giving heir carte blanche  like mbs  
-----------------------------------
 hurricanemichael  tsmichael  michael
-----------------------------------
o all victims of hurricane michael  alive or no more  my hope and prayers will go out to all of you  cling onto hope and don t give in 
---------------------

   dukeenergy our power had been off since      am yesterday in lake park  it is      pm today looks like no one s still come to the site to start working on the down power lines  millbrook and lead mine  dukeenergy  hurricanemichael cc  wralweather  wral  gloriaabc    abc  pic twitter com lrlftgbchg
-----------------------------------
 tyndaleairforcebase looks like this was  targeted  by the  weather  aka haarp hummmmmmm  hurricanemichael
-----------------------------------
lol  raised my little boys to be kind   polite  so  due to hurricane michael  baby boy insisted i spend night of storm with him  so sweet   except for the kemp sign in his yard   my work is never done  the sign does have a dent in the middle after i left 
-----------------------------------
yeah hurricane michael did a hell of a job picking out there 
-----------------------------------
 hurricanemichael  before after
-----------------------------------
yeah  it s hurricane michael
--------------------------------

-----------------------------------
hat  fridayfeeling you get when you survive  hurricanemichael  release a new issue and get to host  dinesouth next thursday  don t forget today the last day to vote in our  southsgreatestkids contest pic twitter com  oizjmthug
-----------------------------------
he devastation in florida from  hurricanemichael is mind boggling  i hope    will do more than throw paper towels at them  
-----------------------------------
why florida skies turned purple after hurricane michael http   a msn com    en us bbogbjg ocid st  
-----------------------------------
wow  hurricane michael tried to be like god by showing up and showing out  whatanight  man there were some moments that really had me worried  all the wind and rain and branches reminded me of when i lost my    
-----------------------------------
hey  remember that time yesterday when you had kanye over to visit while hurricane michael ravaged florida 
-----------------------------------
its a good th

-----------------------------------
      wpap     nb and sb are open   just drove out  sb is one lane in some spots  same as nb  but moving  panamacity  hurricanemichael
-----------------------------------
 hurricanemichael has decided to take a whack at some of our lower lying equipment at  charliesoap  central  but we can swim  stay safe everyone   our thoughts and prayers with all our friends and family in florida and georgia pic twitter com jduz rz vt
-----------------------------------
we all know how much trump  cares  about others with his hurricane responses   hurricanemichael  rememberpuertoricopic twitter com d ibwvpbqf
-----------------------------------
who s getting tired of these goddamn trump kanye tweets  there r more important things   like trumps  tax fraud  saudi arabia murdering its reporters  hurricane michael  russian collusion   mueller investigation  cohen testifying et etc stop this goddamn bullshit on trump kanye 
-----------------------------------
stormy da

-----------------------------------
keeping impacted communities connected  hurricanemichael 
-----------------------------------
so sad i m missing my new york trip due to  hurricanemichael   southwestair they tried to get me there but no luck  trip would have been half over  praying my bag is found and returned to me  southwestairlines  mybagmadeitandididnt
-----------------------------------
anderson cooper calls out trump s hurricane hypocrisy  cnn s anderson cooper criticizes president trump s white house meeting with kanye west while florida simultaneously deals with the fallout from hurricane michael  http   tw eet link qn  kr pic twitter com  q hpxfobc
-----------------------------------
gm everyone  prayers up for those affected by  hurricanemichael aaannd these lost souls  mmm  
-----------------------------------
here are serious communication issues in the  whitehouse too     haiku  lockhimup  puertorico  manafort  witnesstampering  releasethehostages  liarinchief  traitor 

...

   realdonaldtrump held a rally in pennsylvania while the florida panhandle was being destroyed by  hurricanemichael   i have friends and family there  some lost everything but the president doesn t give a crap for anyone but his massive ego   maga you have been conned 
-----------------------------------
hurricane michael is the blow job these weather channel guys have been waiting for 
-----------------------------------
michael langdon thinks he s slick   hurricanemichael  ahsapocalypsepic twitter com guvpinqicd
-----------------------------------
school got cancelled bc hurricane michael   that means f u c k my essay
-----------------------------------
for friends and loved ones concerned about missing family members  miguel marquez reads off the names of people who are safe following  hurricanemichael  
-----------------------------------
 hurricanemichael go way and never come back pic twitter com bx cmhgavc
-----------------------------------
 stfu       hypocrite  hypocrisy  ka

-----------------------------------
 flguard  there are serious communication issues in the panhandle after  hurricanemichael  if you are worried about someone  visit 
-----------------------------------
 flguard  there are serious communication issues in the panhandle after  hurricanemichael  if you are worried about someone  visit 
-----------------------------------
 flguard  there are serious communication issues in the panhandle after  hurricanemichael  if you are worried about someone  visit 
-----------------------------------
 flguard  there are serious communication issues in the panhandle after  hurricanemichael  if you are worried about someone  visit 
-----------------------------------
 flguard  there are serious communication issues in the panhandle after  hurricanemichael  if you are worried about someone  visit 
-----------------------------------
it s been storming all day here in raleigh  windy     of rain  and now the sky is this crazy orangey purple  hurricanemichae

-----------------------------------
 profnichols 
-----------------------------------
sorry senator  why don t you and your colleagues release some defense dept money to  help people affected by hurricane michael    ask the gop sens  up for re election to explain the lack of empathy they have for citizens if they say no  
-----------------------------------
fuck hurricane michael i m sippin some wine
-----------------------------------
hank you for bringing us information about  hurricanemichael  mexicobeach it s just devastating  
-----------------------------------
video shows classic cars  garage ravaged by hurricane michael http   dlvr it qn ljn pic twitter com o t xsjjxc
-----------------------------------
always the meddler  soros groups use  hurricanemichael to push florida  voting rights crisis  scheme  http   bit ly  a jgl 
-----------------------------------
 nailedit we have aftermath of  hurricanemichael   an international incident occurring in real time w regard to  saudis

stuck at home because of hurricane michael  just think there s only    days until the season starts   ravensgbball  everyraveneveryday  leadfromhere  hurricanemichael  seasoncountdown  countdownpic twitter com qitfop  wa
-----------------------------------
 hurricanemichael  treedown  laurenwieds got her wish  now time to cut it up   fuquay varina  north carolina 
-----------------------------------
prayers up for any and everyone affected by  hurricanemichael
-----------------------------------
hurricane michael really trying to fuck the city up  i m sick of this shit  pic twitter com fpivr wudn
-----------------------------------
according to this  johnrich person s twitter feed   yes  now who is he      haiku  lockhimup  manafort  puertorico  hurricanemichael  witnesstampering  releasethehostages  liarinchief  traitor  trumprussiacollusion  muellertime  stolenseat
-----------------------------------
kannapolis power lines down  no injuries   tropicalstormmichael  hurricanemichael  n

i wonder if the people in the fl panhandle give a shit about the neurotic  narcissistic chocolate drama queen attention whore butt kissing his older vanilla spirit animal in the oval office right now         hurricanemichael  thursdaythoughts  kanyewest
-----------------------------------
hello luis  thank you for contacting us   hurricanemichael has impacted a few flights were you able to get onto your flight and to your destination safely   asf
-----------------------------------
 voltramaxllc good news  hurricanemichael 
-----------------------------------
praying for the people being affected by hurricane michael   may god surround them with comfort  peace    strength 
-----------------------------------
it s a little too rainy outside with hurricane michael passing through  but someone s wife should be happy to get her two toned ag   compact in     blackout   sniper  sniperrifle  
-----------------------------------
jacob made me move my car   hurricanemichael pic twitter com hye 

In [38]:
# print informative tweets
mask = michael.inform_pred == 1
for tweet in michael[mask].clean_text:
    print(tweet)
    print('-----------------------------------')

 cotnews has been working      to restore services in tallahassee  thank you  to all the voulenteers and people of this city for everything  you are our heros   hurricanemichael  blessed  unitedwestand  tallahasseeproud
-----------------------------------
in the wake of hurricane michael  we understand the importance of knowing where to find aid  for storm recovery resources  please visit the following link  
-----------------------------------
in other news praying for those affected by hurricane michael
-----------------------------------
 niantichelp when hurricane florence came to the us there was no weather warning but this time i saw it for hurricane michael and it felt good  thank you for making sure we were safe on the east coast this time and during a event  sincerely
-----------------------------------
don t forget the paper towels  as far as water is concerned hurricane michael was very wet 
-----------------------------------
hurricane michael leaves friends  relatives sear

-----------------------------------
new post  st  joe club   resorts northwest florida properties open for business after hurricane michael  has been published on adsbutf   http   adsbutf com            st joe club resorts northwest florida properties open for business after hurricane michael   
-----------------------------------
here s never a good time for a hurricane to hit  but hurricane michael walloped florida last week just before an important federal tax deadline  that s why the irs acted quickly in announcing tax relief for filers facing monday s 
-----------------------------------
my beautiful friend hope and her family lost everything in hurricane michael  every little bit helps  thank you 
-----------------------------------
hurricane michael stole our power and we just got it back  boy i have missed twitter and the news  i ve been in the dark since early wed  afternoon
-----------------------------------
hurricane michael slammed the florida panhandle  it also socked vir

-----------------------------------
communication is critical during crises like  hurricanemichael  read how people are communicating information about the hurricane on social media  
-----------------------------------
hurricane michael live updates     deaths in a vast trail of destruction 
-----------------------------------
abbreviated pundit roundup  trump s disgraceful response to hurricane michael and its aftermath 
-----------------------------------
 panamacity  mexicobeach  hurricanemichael haven t been able to reach my family since evening of the storm  know they made it  i proposed to my wife on mexico beach  we got married in a small church on   th and      holds a special place in our hearts  donate to red cross 
-----------------------------------
hurricane michael strikes days following the fema national test    coincidence   
-----------------------------------
he houses are starting to mold   smell  we re struggling to find tarps to cover roofs for people  hands are r

a big thanks to the  redcross for partnering with us to host a  hurricanemichael disaster relief telethon  call before the end of the day today to donate                to donate online  
-----------------------------------
escuers fear more dead in hurricane michael s path of destruction 
-----------------------------------
escuers fear more dead in hurricane michael s path of destruction http   dlvr it qn  tv pic twitter com s w xajxg 
-----------------------------------
 verizonsupport people in florida are being given  att cellphones because of the  verizon outage  they need help and communication   hurricanemichael
-----------------------------------
watch  florida pastor sings as hurricane michael plows through home http   wfla com            pic twitter com f bqk i xx
-----------------------------------
escuers fear more dead in hurricane michael s path of destruction 
-----------------------------------
   dhsgov and  fema are working closely with all the governors affected by 

 ferrellgas could we get a couple of trucks into  panamacityfl for  hurricanemichael survivors that are cooking outside and need to refill their propane tanks  how would we make that happen  asking for a community of those in need   hurricanemichaelpc
-----------------------------------
here are some pictures of the total devastation in mexico beach  florida  where hurricane michael made landfall  the strong winds and powerfull storm surge caused widespread damage  photo courtesy  alyssahymanmmj via twitter  pic twitter com  jlj nchfq
-----------------------------------
before and after aerial maps show the miles of destruction left by hurricane michael http   dlvr it qn wtj pic twitter com  bxq nekpt
-----------------------------------
watch  animals trapped in shelter after hurricane michael  hurricane michael s heavy winds knocked down trees  blocking the only road to and from the shelter  http   dlvr it qn wxp  impeachtrump  impeachkavanaughpic twitter com lbmdtcxgdq
--------------

...

hurricane michael churned across the florida panhandle  blasting it with     mph winds and a    foot storm surge  
-----------------------------------
him going to a fundraiser and campaign rally instead of overseeing the hurricane michael effort while making said rally goers pay for a ticket into it and pay by their their taxes to fund it   that s sounds just about right
-----------------------------------
oday i was able to shadow the graphic design team while they were designing the graphics for today s show  they were making graphics for the disaster relief of hurricane michael  as well as a school bus crash in pinellas county  pic twitter com rnifcburla
-----------------------------------
i m mad that the owners left this poor man alone to take care of their pets  he promised to protect their dogs during hurricane  michael  then the walls collapsed http   a msn com    en us bbofhhi ocid st    thursdaythoughts
-----------------------------------
not to mention that there are still 

looking to talk to residents from mexico beach  fl   hurricanemichael please dm me contact information 
-----------------------------------
 it s like this storm had eyes   lonnie quinn explains why hurricane michael intensified so quickly http   bit ly  cerrlf pic twitter com dsnq v cgf
-----------------------------------
social media a key conduit for warnings and hope during  hurricanemichael http   dlvr it qn dk  pic twitter com elsdqhrgss
-----------------------------------
listen to our thursday news update  news anchor rahul bali has the latest on damage assessments and power restoration efforts after what was left of hurricane michael moved through the lake area  
-----------------------------------
hurricane michael is crazy   we re in nc and it s hitting us hard  i can t imagine how bad it was for those in florida and georgia  my prayers go out to everyone effected by this 
-----------------------------------
      mic drop  joe bastardi shreds bette midler s climate change  

-----------------------------------
ain is heading this way from hurricane michael http   brooklyn news   com story          forecast heavy rain douses area as remnants of michael move in  
-----------------------------------
i liked a  youtube video http   youtu be  f u hyuhmi a pink bucket nation presents  hurricane michael watch lego stream  
-----------------------------------
he city of lawrenceville electric department is happy to offer mutual aid to thomasville  georgia  where three substations and    main line circuits are currently out due to hurricane michael   happytohelp http   ow ly  lnh  mceiq pic twitter com vrimztwchr
-----------------------------------
 looking outside at hurricane michael   me  ryan look at the wind ryan  i don t see wind  i just see trees moving me  pic twitter com clcgdbuvf 
-----------------------------------
 hurricane michael is the most intense hurricane to make landfall since camille in           riskpulse  watch their webinar for an impact upd

hurricane michael devastation in panama city  florida seen in drone video  photos 
-----------------------------------
just received a briefing from state officials on the damage caused by hurricane michael  our prayers are with the victims  first responders  and relief workers  we will rebuild   gapolpic twitter com eccb qsxld
-----------------------------------
hurricane michael like  oh y all thought florence was suppose to hit  it s okay    i got you  pic twitter com fhyfijyqoi
-----------------------------------
president trump s live interview on hurricane michael kayne west and prison reform   maga  trump  trns 
-----------------------------------
 it s absolutely horrendous    florida residents detail  hurricanemichael s catastrophic destruction  http   bit ly  iolww  pic twitter com b hqz pky 
-----------------------------------
waffle house forced to close due to hurricane michael 
-----------------------------------
in the aftermath of  hurricanemichael here are the observat

-----------------------------------
hurricane michael leaves trail of destruction as it slams florida s panhandle 
-----------------------------------
we are assembling a storm response team to aid those affected by hurricane michael   floridastrong  servpro  helpisontheway
-----------------------------------
striking photos and video from hurricane michael s path of destruction http   dlvr it qn cbm pic twitter com sy  cotqgj
-----------------------------------
 hurricane michael leaves trail of destruction as it slams florida s panhandle  by richard fausset  alan blinder and patricia mazzei via nyt 
-----------------------------------
 hurricane michael leaves trail of destruction as it slams florida s panhandle  by richard fausset  alan blinder and patricia mazzei via nyt 
-----------------------------------
we would like to reach out to everyone in the aftermath of hurricane michael  although we ve been very fortunate in destin miramar beach  our fellow communities like panama city

In [ ]:
# should probably keep numbers in the cleaned tweets
# we have some non-English tweets
# only 1/5 tweets were marked as uninformative - does not help to narrow down the stream much
